In [1]:
! pip install emoji contractions

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 397.5/397.5 kB 5.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 289.9/289.9 kB 29.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 110.8/110.8 kB 14.4 MB/s eta 0:00:00


In [2]:
import pandas as pd
from tqdm.notebook import trange, tqdm

In [3]:
# replace user tags with @user, consecutive whitespaces to single space,
# surround punctuations with space as in https://aclanthology.org/2022.semeval-1.133.pdf
# also replace emojis with text desc using 'emoji'
# !pip install emoji contractions

import re
import emoji
import contractions

def expand_contractions(text):
    expanded_text = contractions.fix(text)
    return expanded_text

def preprocess_tweet(tweet):
  # Replace tagged users with @user
  tweet = re.sub(r'@[\w]+', '@user', str(tweet))

  # Replace multiple white spaces with a single space
  tweet = re.sub(r'\s+', ' ', tweet)

  # Remove more than two successive occurrences of any punctuation
  tweet = re.sub(r'(\s*([.,!?;:()<>{}[\]\-+=~_$%^&]\s){2,})', r'\1', tweet)

  # Replace emoji with emoji descriptor
  tweet = emoji.demojize(tweet)

  # Put a single white space around punctuations
  tweet = re.sub(r'([.,!?;:()<>{}[\]\-+=~_$%^&*])', r' \1 ', tweet)

  # expand contractions
  tweet = expand_contractions(tweet)

  return tweet

In [4]:
data = pd.read_csv('/content/isarcasmeval_train.csv', index_col=0)
data['tweet'] = data['tweet'].apply(preprocess_tweet)
data['rephrase'] = data['rephrase'].apply(preprocess_tweet)
data

tweet  sarcastic  \
0     The only thing I got from college is a caffein...          1   
1     I love it when professors draw a big question ...          1   
2     Remember the hundred emails from companies whe...          1   
3     Today my pop - pop told me I was not “forced” ...          1   
4     @user @user @user I did too ,  and I also repo...          1   
...                                                 ...        ...   
3463  The population spike in Chicago in 9 months is...          0   
3464  You would think in the second to last English ...          0   
3465  I am finally surfacing after a holiday to Scot...          0   
3466  Could not be prouder today .  Well done to eve...          0   
3467  Overheard as my 13 year old games with a frien...          0   

                                               rephrase  sarcasm  irony  \
0     College is really difficult ,  expensive ,  ti...      0.0    1.0   
1     I do not like when professors do not write out...      1.0    0.0   
2     I ,  at the bare minimum ,  wish companies act...      0.0    1.0   
3     Today my pop - pop told me I was not "forced" ...      1.0    0.0   
4     I would say Ted Cruz is an asshole and does no...      1.0    0.0   
...                                                 ...      ...    ...   
3463                                                nan      NaN    NaN   
3464                                                nan      NaN    NaN   
3465                                                nan      NaN    NaN   
3466                                                nan      NaN    NaN   
3467                                                nan      NaN    NaN   

      satire  understatement  overstatement  rhetorical_question  
0        0.0             0.0            0.0                  0.0  
1        0.0             0.0            0.0                  0.0  
2        0.0             0.0            0.0                  0.0  
3        0.0             0.0            0.0                  0.0  
4        0.0             0.0            0.0                  0.0  
...      ...             ...            ...                  ...  
3463     NaN             NaN            NaN                  NaN  
3464     NaN             NaN            NaN                  NaN  
3465     NaN             NaN            NaN                  NaN  
3466     NaN             NaN            NaN                  NaN  
3467     NaN             NaN            NaN                  NaN  

[3468 rows x 9 columns]

In [5]:
data['tweet'][3000]

'Motivation Wednesday Night :  I AM the powerhouse of the cell . '

## LLM with Zero Shot Learning

## LLM = T5

### Sub-task A

In [6]:
from transformers import AutoModelForSeq2SeqLM, AutoTokenizer

model_name = "t5-base"
model = AutoModelForSeq2SeqLM.from_pretrained(model_name)
tokenizer = AutoTokenizer.from_pretrained(model_name)

config.json:   0%|          | 0.00/1.21k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/892M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/147 [00:00<?, ?B/s]

spiece.model:   0%|          | 0.00/792k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.39M [00:00<?, ?B/s]

/usr/local/lib/python3.10/dist-packages/transformers/models/t5/tokenization_t5_fast.py:160: FutureWarning: This tokenizer was incorrectly instantiated with a model max length of 512 which will be corrected in Transformers v5.
For now, this behavior is kept to avoid breaking backwards compatibility when padding/encoding with `truncation is True`.
- Be aware that you SHOULD NOT rely on t5-base automatically truncating your input to 512 when padding/encoding.
- If you want to encode/pad to sequences longer than 512 you can either instantiate this tokenizer with `model_max_length` or pass `max_length` when encoding/padding.
- To avoid this warning, please instantiate this tokenizer with `model_max_length` set to your preferred value.
  warnings.warn(


In [7]:
prompt = '''Here are 4 examples of Sarcastic and Not Sarcastic sentences:\n
            Sentence: The only thing I got from college is a caffeine addiction
            Output: True

            Sentence: I love it when professors draw a big question mark next to my answer on an exam because I am always like yeah I do not either ¯\ _  ( ツ )  _ /¯
            Output: True

            Sentence: 2br apt ,  Notts city centre https : //t . co/yFj989BdXR
            Output: False

            Sentence: Motivation Wednesday Night :  I AM the powerhouse of the cell .
            Output: False

            For the task of Sarcasm Detection, choose whether the following sentence is Sarcastic OR Not Sarcastic. \n'''


count = 0
for i in trange(len(data)):
  input_text = data['tweet'][i]
  input_ids = tokenizer.encode(prompt + input_text, return_tensors="pt")
  output_ids = model.generate(input_ids)
  output_text = tokenizer.decode(output_ids[0], skip_special_tokens=True)
  print(output_text)
  if output_text and data['sarcastic'][i] == 1:
    count+=1

print(count)

  0%|          | 0/3468 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/transformers/generation/utils.py:1273: UserWarning: Using the model-agnostic default `max_length` (=20) to control the generation length. We recommend setting `max_new_tokens` to control the maximum length of the generation.
  warnings.warn(


True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True


In [26]:
len(data)

3468

In [8]:
867/3468

0.25

In [62]:
# prompt = '''The capital of France'''
input_text = data['tweet'][3100]
input_ids = tokenizer.encode(prompt + input_text, return_tensors="pt")

count = 0
output_ids = model.generate(input_ids)
output_text = tokenizer.decode(output_ids[0], skip_special_tokens=True)
print(output_text)

True


In [8]:
prompt = '''There are 6 types of sarcasm - "sarcasm, irony, satire, understatement, overstatement, rhetorical_question"
            Here are 6 examples of sentences and their types:
            Sentence: The only thing I got from college is a caffeine addiction
            Output: irony

            Sentence: Ok ,  so @user and I decided to record on the evening of the 6th ,  just as absolutely nothing newsworthy was happening !  Perfect timing as always ,  to go over some of the best ITSBUPs of 2020  -  and how we are settling into 2021 !  Listen :  https : //t . co/oaPLwrtcHP https : //t . co/za3EHuqcWh
            Output: sarcasm

            Sentence: @user Do I need to aquire a wife before this happens or will I be assigned one ?
            Output: rhetorical_question, sarcasm

            Sentence: 6 more hours and then a whoppingly massive 2days off work !  wowzers !
            Output: overstatement, irony

            Sentence: Lucky for 2nd placed Brentford that there is no stand out team like Leeds this year ,  or they might have no chance of winning the league .  #ncfc
            Output: understatement, sarcasm

            Sentence: Thinking about that time Blizzard had the brilliant idea to change everyone is name on their forums to their real names .  God ,  what an idea that was .
            Output: satire, sarcasm

            Remember each sentence can have multiple types.
            Which of the types of sarcasm the following sentence belongs to? \n'''

input_text = data['tweet'][80]
input_ids = tokenizer.encode(prompt + input_text, return_tensors="pt")

count = 0
output_ids = model.generate(input_ids)
output_text = tokenizer.decode(output_ids[0], skip_special_tokens=True)
print(output_text)

sarcasm, irony, satire, understatement, over


## GPT3 Zero Shot Learning

## Sub-task A

In [9]:
from transformers import pipeline
import numpy as np
import torch

device = 'cuda' if torch.cuda.is_available() else 'cpu'

model_name = "EleutherAI/gpt-neo-1.3B"
zero_shot_classifier = pipeline("zero-shot-classification", model=model_name, device=device)

prompt = '''Here are 4 examples of Sarcastic and Not Sarcastic sentences:
            Sentence: The only thing I got from college is a caffeine addiction
            Output: Sarcastic

            Sentence: I love it when professors draw a big question mark next to my answer on an exam because I am always like yeah I do not either ¯\ _  ( ツ )  _ /¯
            Output: Sarcastic

            Sentence: 2br apt ,  Notts city centre https : //t . co/yFj989BdXR
            Output: Not Sarcastic

            Sentence: Motivation Wednesday Night :  I AM the powerhouse of the cell .
            Output: Not Sarcastic

            For the task of Sarcasm Detection, choose whether the following sentence is Sarcastic OR Not Sarcastic. \n'''

candidate_labels = ['Sarcastic','Not Sarcastic']

count = 0
for i in range(len(data)):
  input_text = data['tweet'][i]
  true = data['sarcastic'][i]

  result = zero_shot_classifier(prompt+input_text, candidate_labels)
  pred = result['labels'][np.argmax(result['scores'])]

  if pred == 'Sarcastic' and true == 1:
    count+=1
  elif pred == 'Not Sarcastic' and true == 0:
    count+=1
  print(np.argmax(result['scores']))
  print(result)
  print(pred)

Some weights of GPTNeoForSequenceClassification were not initialized from the model checkpoint at EleutherAI/gpt-neo-1.3B and are newly initialized: ['score.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Failed to determine 'entailment' label id from the label2id mapping in the model config. Setting to -1. Define a descriptive label2id mapping in the model config to ensure correct outputs.
Tokenizer was not supporting padding necessary for zero-shot, attempting to use  `pad_token=eos_token`


0
{'sequence': 'Here are 4 examples of Sarcastic and Not Sarcastic sentences:\n            Sentence: The only thing I got from college is a caffeine addiction\n            Output: Sarcastic\n            \n            Sentence: I love it when professors draw a big question mark next to my answer on an exam because I am always like yeah I do not either ¯\\ _  ( ツ )  _ /¯ \n            Output: Sarcastic\n\n            Sentence: 2br apt ,  Notts city centre https : //t . co/yFj989BdXR\n            Output: Not Sarcastic\n            \n            Sentence: Motivation Wednesday Night :  I AM the powerhouse of the cell .\n            Output: Not Sarcastic\n            \n            For the task of Sarcasm Detection, choose whether the following sentence is Sarcastic OR Not Sarcastic. \nThe only thing I got from college is a caffeine addiction', 'labels': ['Sarcastic', 'Not Sarcastic'], 'scores': [0.5182067155838013, 0.48179328441619873]}
Sarcastic
0
{'sequence': 'Here are 4 examples of Sarcas

/usr/local/lib/python3.10/dist-packages/transformers/pipelines/base.py:1101: UserWarning: You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset
  warnings.warn(


Streaming output truncated to the last 5000 lines.
{'sequence': 'Here are 4 examples of Sarcastic and Not Sarcastic sentences:\n            Sentence: The only thing I got from college is a caffeine addiction\n            Output: Sarcastic\n            \n            Sentence: I love it when professors draw a big question mark next to my answer on an exam because I am always like yeah I do not either ¯\\ _  ( ツ )  _ /¯ \n            Output: Sarcastic\n\n            Sentence: 2br apt ,  Notts city centre https : //t . co/yFj989BdXR\n            Output: Not Sarcastic\n            \n            Sentence: Motivation Wednesday Night :  I AM the powerhouse of the cell .\n            Output: Not Sarcastic\n            \n            For the task of Sarcasm Detection, choose whether the following sentence is Sarcastic OR Not Sarcastic. \n@user @user All/any updates are fully appreciated Mike .  Many thanks', 'labels': ['Not Sarcastic', 'Sarcastic'], 'scores': [0.517257571220398, 0.482742398977279

In [10]:
print(count)

1986


In [11]:
count/len(data)

0.5726643598615917

In [52]:
data

tweet  sarcastic  \
0     The only thing I got from college is a caffein...          1   
1     I love it when professors draw a big question ...          1   
2     Remember the hundred emails from companies whe...          1   
3     Today my pop - pop told me I was not “forced” ...          1   
4     @user @user @user I did too ,  and I also repo...          1   
...                                                 ...        ...   
3463  The population spike in Chicago in 9 months is...          0   
3464  You would think in the second to last English ...          0   
3465  I am finally surfacing after a holiday to Scot...          0   
3466  Could not be prouder today .  Well done to eve...          0   
3467  Overheard as my 13 year old games with a frien...          0   

                                               rephrase  sarcasm  irony  \
0     College is really difficult ,  expensive ,  ti...      0.0    1.0   
1     I do not like when professors do not write out...      1.0    0.0   
2     I ,  at the bare minimum ,  wish companies act...      0.0    1.0   
3     Today my pop - pop told me I was not "forced" ...      1.0    0.0   
4     I would say Ted Cruz is an asshole and does no...      1.0    0.0   
...                                                 ...      ...    ...   
3463                                                nan      NaN    NaN   
3464                                                nan      NaN    NaN   
3465                                                nan      NaN    NaN   
3466                                                nan      NaN    NaN   
3467                                                nan      NaN    NaN   

      satire  understatement  overstatement  rhetorical_question  
0        0.0             0.0            0.0                  0.0  
1        0.0             0.0            0.0                  0.0  
2        0.0             0.0            0.0                  0.0  
3        0.0             0.0            0.0                  0.0  
4        0.0             0.0            0.0                  0.0  
...      ...             ...            ...                  ...  
3463     NaN             NaN            NaN                  NaN  
3464     NaN             NaN            NaN                  NaN  
3465     NaN             NaN            NaN                  NaN  
3466     NaN             NaN            NaN                  NaN  
3467     NaN             NaN            NaN                  NaN  

[3468 rows x 9 columns]

In [50]:
tmp = data[data['sarcastic'] == 1].drop(labels=['tweet', 'sarcastic', 'rephrase'], axis=1)
tmp.columns[tmp.iloc[1].isin([1])].to_list()

['sarcasm']

### Sub-task B

In [31]:
data['tweet'][426]

'Thinking about that time Blizzard had the brilliant idea to change everyone is name on their forums to their real names .  God ,  what an idea that was . '

In [32]:
data.loc[426]

tweet                  Thinking about that time Blizzard had the bril...
sarcastic                                                              1
rephrase               "The idea Blizzard had to stop people from bei...
sarcasm                                                              1.0
irony                                                                0.0
satire                                                               1.0
understatement                                                       0.0
overstatement                                                        0.0
rhetorical_question                                                  0.0
Name: 426, dtype: object

In [54]:
from transformers import pipeline
import numpy as np
import torch

device = 'cuda' if torch.cuda.is_available() else 'cpu'

model_name = "EleutherAI/gpt-neo-1.3B"
zero_shot_classifier = pipeline("zero-shot-classification", model=model_name, device=device)

prompt = '''There are 6 types of sarcasm - sarcasm, irony, satire, understatement, overstatement, rhetorical_question
            Here are 6 examples of sentences and their types:
            Sentence: The only thing I got from college is a caffeine addiction
            Output: irony

            Sentence: Ok ,  so @user and I decided to record on the evening of the 6th ,  just as absolutely nothing newsworthy was happening !  Perfect timing as always ,  to go over some of the best ITSBUPs of 2020  -  and how we are settling into 2021 !  Listen :  https : //t . co/oaPLwrtcHP https : //t . co/za3EHuqcWh
            Output: sarcasm

            Sentence: @user Do I need to aquire a wife before this happens or will I be assigned one ?
            Output: rhetorical_question, sarcasm

            Sentence: 6 more hours and then a whoppingly massive 2days off work !  wowzers !
            Output: overstatement, irony

            Sentence: Lucky for 2nd placed Brentford that there is no stand out team like Leeds this year ,  or they might have no chance of winning the league .  #ncfc
            Output: understatement, sarcasm

            Sentence: Thinking about that time Blizzard had the brilliant idea to change everyone is name on their forums to their real names .  God ,  what an idea that was .
            Output: satire, sarcasm

            Remember each sentence can have multiple types.
            For the task of Sarcasm Detection, choose which of the types of sarcasm the following sentence belongs to. \n'''

candidate_labels = ['sarcasm',	'irony',	'satire',	'understatement',	'overstatement',	'rhetorical_question']

count = 0
for i in range(len(data[data['sarcastic'] == 1])):
  input_text = data['tweet'][i]

  tmp = data[data['sarcastic'] == 1].drop(labels=['tweet', 'sarcastic', 'rephrase'], axis=1)
  true = tmp.columns[tmp.iloc[i].isin([1])].to_list()
  print('true', true)

  result = zero_shot_classifier(prompt+input_text, candidate_labels)
  pred = result['labels'][np.argmax(result['scores'])]

  if pred in true:
    count+=1
    print('yes')
  # elif pred == 'irony' and true == 1:
  #   count+=1
  # elif pred == 'satire' and true == 2:
  #   count+=1
  # elif pred == 'understatement' and true == 1:
  #   count+=1
  # elif pred == 'overstatement' and true == 1:
  #   count+=1
  # elif pred == 'rhetorical_question' and true == 1:
  #   count+=1
  # print(result['labels'][np.argmax(result['scores'])])
  print(result)
  print(pred)

# input_text = data['tweet'][10]

# result = zero_shot_classifier(prompt+input_text, candidate_labels)
# print(result)

Some weights of GPTNeoForSequenceClassification were not initialized from the model checkpoint at EleutherAI/gpt-neo-1.3B and are newly initialized: ['score.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Failed to determine 'entailment' label id from the label2id mapping in the model config. Setting to -1. Define a descriptive label2id mapping in the model config to ensure correct outputs.
Tokenizer was not supporting padding necessary for zero-shot, attempting to use  `pad_token=eos_token`


true ['irony']
rhetorical_question
{'sequence': 'There are 6 types of sarcasm - sarcasm, irony, satire, understatement, overstatement, rhetorical_question\n            Here are 6 examples of sentences and their types:\n            Sentence: The only thing I got from college is a caffeine addiction\n            Output: irony\n            \n            Sentence: Ok ,  so @user and I decided to record on the evening of the 6th ,  just as absolutely nothing newsworthy was happening !  Perfect timing as always ,  to go over some of the best ITSBUPs of 2020  -  and how we are settling into 2021 !  Listen :  https : //t . co/oaPLwrtcHP https : //t . co/za3EHuqcWh\n            Output: sarcasm\n\n            Sentence: @user Do I need to aquire a wife before this happens or will I be assigned one ? \n            Output: rhetorical_question, sarcasm\n            \n            Sentence: 6 more hours and then a whoppingly massive 2days off work !  wowzers ! \n            Output: overstatement, iron

/usr/local/lib/python3.10/dist-packages/transformers/pipelines/base.py:1101: UserWarning: You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset
  warnings.warn(


satire
{'sequence': 'There are 6 types of sarcasm - sarcasm, irony, satire, understatement, overstatement, rhetorical_question\n            Here are 6 examples of sentences and their types:\n            Sentence: The only thing I got from college is a caffeine addiction\n            Output: irony\n            \n            Sentence: Ok ,  so @user and I decided to record on the evening of the 6th ,  just as absolutely nothing newsworthy was happening !  Perfect timing as always ,  to go over some of the best ITSBUPs of 2020  -  and how we are settling into 2021 !  Listen :  https : //t . co/oaPLwrtcHP https : //t . co/za3EHuqcWh\n            Output: sarcasm\n\n            Sentence: @user Do I need to aquire a wife before this happens or will I be assigned one ? \n            Output: rhetorical_question, sarcasm\n            \n            Sentence: 6 more hours and then a whoppingly massive 2days off work !  wowzers ! \n            Output: overstatement, irony\n\n            Sentence: L

/usr/local/lib/python3.10/dist-packages/transformers/pipelines/base.py:1101: UserWarning: You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset
  warnings.warn(


...

satire
{'sequence': 'There are 6 types of sarcasm - sarcasm, irony, satire, understatement, overstatement, rhetorical_question\n            Here are 6 examples of sentences and their types:\n            Sentence: The only thing I got from college is a caffeine addiction\n            Output: irony\n            \n            Sentence: Ok ,  so @user and I decided to record on the evening of the 6th ,  just as absolutely nothing newsworthy was happening !  Perfect timing as always ,  to go over some of the best ITSBUPs of 2020  -  and how we are settling into 2021 !  Listen :  https : //t . co/oaPLwrtcHP https : //t . co/za3EHuqcWh\n            Output: sarcasm\n\n            Sentence: @user Do I need to aquire a wife before this happens or will I be assigned one ? \n            Output: rhetorical_question, sarcasm\n            \n            Sentence: 6 more hours and then a whoppingly massive 2days off work !  wowzers ! \n            Output: overstatement, irony\n\n            Sentence: L

/usr/local/lib/python3.10/dist-packages/transformers/pipelines/base.py:1101: UserWarning: You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset
  warnings.warn(


satire
{'sequence': 'There are 6 types of sarcasm - sarcasm, irony, satire, understatement, overstatement, rhetorical_question\n            Here are 6 examples of sentences and their types:\n            Sentence: The only thing I got from college is a caffeine addiction\n            Output: irony\n            \n            Sentence: Ok ,  so @user and I decided to record on the evening of the 6th ,  just as absolutely nothing newsworthy was happening !  Perfect timing as always ,  to go over some of the best ITSBUPs of 2020  -  and how we are settling into 2021 !  Listen :  https : //t . co/oaPLwrtcHP https : //t . co/za3EHuqcWh\n            Output: sarcasm\n\n            Sentence: @user Do I need to aquire a wife before this happens or will I be assigned one ? \n            Output: rhetorical_question, sarcasm\n            \n            Sentence: 6 more hours and then a whoppingly massive 2days off work !  wowzers ! \n            Output: overstatement, irony\n\n            Sentence: L

/usr/local/lib/python3.10/dist-packages/transformers/pipelines/base.py:1101: UserWarning: You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset
  warnings.warn(


satire
{'sequence': 'There are 6 types of sarcasm - sarcasm, irony, satire, understatement, overstatement, rhetorical_question\n            Here are 6 examples of sentences and their types:\n            Sentence: The only thing I got from college is a caffeine addiction\n            Output: irony\n            \n            Sentence: Ok ,  so @user and I decided to record on the evening of the 6th ,  just as absolutely nothing newsworthy was happening !  Perfect timing as always ,  to go over some of the best ITSBUPs of 2020  -  and how we are settling into 2021 !  Listen :  https : //t . co/oaPLwrtcHP https : //t . co/za3EHuqcWh\n            Output: sarcasm\n\n            Sentence: @user Do I need to aquire a wife before this happens or will I be assigned one ? \n            Output: rhetorical_question, sarcasm\n            \n            Sentence: 6 more hours and then a whoppingly massive 2days off work !  wowzers ! \n            Output: overstatement, irony\n\n            Sentence: L

In [55]:
print(count)

41


In [57]:
count/len(data[data['sarcastic'] == 1])

0.04728950403690888